In [1]:
import jsonlines
import re
import urllib.parse

In [2]:
def parse_question(match, pagetitle, url):
    question = match.group('question').replace('<br> ', '').strip()
    params = [p for p in match.group('info').strip('{}').split('|') if p != '']
    if params[0] not in ['Kvízkérdés', 'kvízkérdés']:
        print(params[0])
        return None
    params_dict = {p.split('=')[0]: p.split('=')[1] for p in params[1:]}
    title = match.group('title').strip()
    filepart = None
    if '[[' in question:
        filepart = re.search(r'\[\[.+\]\]', question)[0]
        question = question.replace(filepart, '').strip()
        filepart = filepart.strip('[]')
    type = {'egy': 'single', 'több': 'multi'}[params_dict['típus']]
    answer = params_dict['válasz']
    if '-' in answer or '/' in answer:
        return None
    score = None
    if 'pont' in params_dict:
        score = params_dict['pont']
    if 'pontozás' in params_dict:
        score = params_dict['pontozás']
    answers = [a.strip('# ') for a in match.group('answers').split('\n') if a.strip('# ') != '']
    #print(answer)
    return {
        'title': title,
        'question': question, 
        'answers': answers, 
        'correct_answers': [int(a) if a.isnumeric() else ord(a.strip())-ord('a')+1 for a in answer.split(',') if a != ''] if answer != '*' else [a+1 for a in range(len(answers))],
        'type': type, 
        'score': score,
        'quiz_title': str(urllib.parse.unquote(pagetitle)), 
        'url': url,
        'file': filepart,
    }

In [3]:
regex = r"==(?P<title>.+)==$\n*(?P<question>(?:[^\=]*\n)*?)\n*{{(?P<info>Kvízkérdés|.+)}}\n*(?P<answers>(?:#.+\n?)+)\n*(?P<footnote>.+\n)*?(?=\n*==)"

In [4]:
data = []
with jsonlines.open('kikerdezok.jsonl') as reader:
    for obj in reader:
        text = obj['text']
        matches = re.finditer(regex, text, re.MULTILINE)
        if not matches:
            continue
        #print(list(matches))
        
        title = obj['url'].strip('/').split('/')[-1]
        questions = [e.strip() for e in text.split('\n\n') if 'Kvízkérdés' in e]
        parsed_questions = [parse_question(m, title, obj['url']) for m in matches]
        data += [p for p in parsed_questions if p]

In [5]:
len([d for d in data if d['question']])

132

In [6]:
len([d for d in data if d['file']])

46

In [7]:
len(data)

8225

In [8]:
with jsonlines.open('kvizek.jsonl', mode='w') as writer:
    for d in data:
        writer.write(d)